A small notebook explaining the pitfalls of algorithmic compexities and the difference of complexity and actual runtime.

First, let's define a few mockup functions whose performance we want to analyze.

In [1]:
# mockup for a function with linear runtime:
# it simply performs a multiplication on the input parameters
# this function has constant runtime,
# basically just the costs for one multiplication
def foo(i,j):
    return i*j

# mockup for a function with linear runtime:
# this function calls function <func> n times
def loop(n, func):
    sum = 0
    for i in range(n):
        sum += func(i,i)
    return sum

# mockup for a function with quadratic runtime:
# this function calls function <func> n*n times
def nestedLoop(n, func):
    sum = 0
    for i in range(n):
        for j in range(n):
            sum += func(i,j)
    return sum

# mockup for a function with n*log n runtime:
# this function calls function <func> n*ceil(log_2 n) times
import math
def loopLog(n, func):
    sum = 0
    _log = math.ceil(math.log2(n))
    for i in range(n):
        for j in range(_log):
            sum += func(i,j)
    return sum

In [2]:
# list files in current directory greater than 1MB
# we do this to simulate I/O operations to play with:
import os
files = [(f,os.stat(f).st_size) for f in os.listdir('.') if os.path.isfile(f) and os.stat(f).st_size >1024*1024]
print(files)

# a mockup function performing a pseudo-random read to simulate I/O:
def foo_IO(i,j):
    # pick a file pseudo-randomly from the pre-computed list of files:
    pseudo_random = i*i % len(files)
    with open(files[pseudo_random][0], 'rb') as f:
        # seek to random offset in that file:
        f.seek(files[pseudo_random][1]//2)
        # read 4096 bytes and return the last byte read:
        first_bytes = f.read(4096)
        # return the bytes read:
        return first_bytes[min(4095,len(first_bytes)-1)]

[('23 Databases.pdf', 100938180), ('24 Database Indexing.pdf', 9474897), ('geonamesGermany.db', 19877888), ('geonamesWorld.db', 3217985536), ('24 Databases 2.pdf', 95571426), ('slide collection.pdf', 19056675), ('geonames.db', 13127680)]


Let's run performance measurements on these mockup functions:

In [11]:
import time
from tqdm import tqdm
# combination of methods to benchmark:
# syntax: (outer-function, inner-function)
methods=[ (loop,foo), (loop, foo_IO), (loopLog, foo), (nestedLoop, foo)]
results = []
for m in tqdm(methods):
    # vary n:
    for n in range(100, 10000, 500):
        start = time.time()
        # call the function combination:
        m[0](n, m[1])
        elapsedTime = time.time() - start
        # append measured times to measurement data:
        results.append((m[0].__name__, m[1].__name__, n, elapsedTime))

100%|██████████| 4/4 [02:30<00:00, 37.74s/it]


Let's display the performance results visually:

In [12]:
import altair as alt
alt.renderers.enable('default')
import pandas as pd

# display all methods:
# convert the <results> array to a pandas dataframe (a table-like structure)
resultsPD = pd.DataFrame(results, columns=['method', 'foo', 'n', 'time'])

# map the columns of resultsPD to x, y, and color
alt.Chart(resultsPD).transform_calculate(
    cat="datum.method + ' using ' + datum.foo"
).mark_line().encode(
    x='n',
    y=alt.Y('time', title='Time [sec]'),
    color=alt.Y('cat:N', title='Algorithm'),
).interactive()

alt.Chart(...)

In [13]:
# display the data as a table:
resultsPD

method     foo     n       time
0         loop     foo   100   0.000022
1         loop     foo   600   0.000115
2         loop     foo  1100   0.000212
3         loop     foo  1600   0.000329
4         loop     foo  2100   0.000456
5         loop     foo  2600   0.000631
6         loop     foo  3100   0.000710
7         loop     foo  3600   0.001056
8         loop     foo  4100   0.000920
9         loop     foo  4600   0.000984
10        loop     foo  5100   0.001076
11        loop     foo  5600   0.001218
12        loop     foo  6100   0.001297
13        loop     foo  6600   0.001538
14        loop     foo  7100   0.001701
15        loop     foo  7600   0.001557
16        loop     foo  8100   0.001590
17        loop     foo  8600   0.002141
18        loop     foo  9100   0.002713
19        loop     foo  9600   0.002756
20        loop  foo_IO   100   0.081536
21        loop  foo_IO   600   0.317835
22        loop  foo_IO  1100   0.619442
23        loop  foo_IO  1600   0.868462
24        loop  foo_IO  2100   1.310503
25        loop  foo_IO  2600   1.337442
26        loop  foo_IO  3100   1.949107
27        loop  foo_IO  3600   1.842671
28        loop  foo_IO  4100   2.496762
29        loop  foo_IO  4600   2.363623
..         ...     ...   ...        ...
50     loopLog     foo  5100   0.010870
51     loopLog     foo  5600   0.011373
52     loopLog     foo  6100   0.012416
53     loopLog     foo  6600   0.013374
54     loopLog     foo  7100   0.014763
55     loopLog     foo  7600   0.016620
56     loopLog     foo  8100   0.017865
57     loopLog     foo  8600   0.020082
58     loopLog     foo  9100   0.021278
59     loopLog     foo  9600   0.022612
60  nestedLoop     foo   100   0.001494
61  nestedLoop     foo   600   0.058755
62  nestedLoop     foo  1100   0.187786
63  nestedLoop     foo  1600   0.379069
64  nestedLoop     foo  2100   0.656695
65  nestedLoop     foo  2600   1.002432
66  nestedLoop     foo  3100   1.430429
67  nestedLoop     foo  3600   1.918911
68  nestedLoop     foo  4100   2.481861
69  nestedLoop     foo  4600   3.122974
70  nestedLoop     foo  5100   3.842251
71  nestedLoop     foo  5600   4.654332
72  nestedLoop     foo  6100   5.514337
73  nestedLoop     foo  6600   6.439412
74  nestedLoop     foo  7100   7.525950
75  nestedLoop     foo  7600   8.576376
76  nestedLoop     foo  8100   9.769704
77  nestedLoop     foo  8600  10.942160
78  nestedLoop     foo  9100  12.338416
79  nestedLoop     foo  9600  13.721358

[80 rows x 4 columns]

feel free to ignore the following...

In [14]:
# helper to be able to tun SQL against pandas data frames:
import pandasql as pdsql
pysql = lambda q: pdsql.sqldf(q, globals())
import sqlparse

def queryFrame(q, _display=False):
    result = pysql(q)
    if _display:
        display(result)
    return result

In [15]:
# calculate performance difference of different methods as a facor:
improvementFactor = queryFrame("""
WITH justfoo AS (
    SELECT *
    FROM resultsPD
    WHERE method='loop' AND foo='foo'),
justRead AS (
    SELECT *
    FROM resultsPD
    WHERE method='loop' AND foo='foo_IO')

SELECT L.n, R.time/L.time as improvementFactor
FROM justfoo L JOIN justRead R
ON L.n==R.n
;
""", True)

n  improvementFactor
0    100        3717.250000
1    600        2765.761411
2   1100        2922.528684
3   1600        2641.474257
4   2100        2874.815377
5   2600        2119.243672
6   3100        2744.258812
7   3600        1745.026643
8   4100        2714.406169
9   4600        2401.587694
10  5100        2871.944826
11  5600        2582.279757
12  6100        2809.156221
13  6600        2338.003876
14  7100        2576.578918
15  7600        2897.216386
16  8100        3050.040636
17  8600        2155.897439
18  9100        1999.917392
19  9600        2064.794896

In [16]:
# draw the improvement factor:
# this graph shows the "slow donw" of the method without I/O over the one with I/O
alt.Chart(improvementFactor).mark_line().encode(
    x='n',
    y=alt.Y('improvementFactor', title='improvement factor')
)

alt.Chart(...)